# Tom Deposit Exploration

In [ ]:
import pandas as pd
import geolime as geo
from pyproj import CRS
import pyvista as pv
import rioxarray
import numpy as np

geo.Project().set_crs(CRS("EPSG:26909"))
pv.set_jupyter_backend("html")

## Drillholes CSV Loading

In [ ]:
assay_tom = pd.read_csv("../data/assay_tom.csv")
collar_tom = pd.read_csv("../data/collar_tom.csv")
survey_tom = pd.read_csv("../data/survey_tom.csv")

In [ ]:
collar_tom

In [ ]:
assay_tom

In [ ]:
survey_tom

## Topo DXF Loading

In [ ]:
tom_topo = geo.surface_from_dxf("Tom", "../data/Topo/TOM_Topo_DEM_Downsampled.dxf")

## GeoLime Drillholes creation

Creation of a Drillholes object using the collar, assay & survey DataFrame. As the holes are deviated we use the minimum curvature method for the desurveying. In the collar file the Z information is provided as Elevation and we have to specify it as GeoLime does not recognizes it by default.

In [ ]:
dh_tom = geo.create_drillholes(
    name="Tom", 
    collar=collar_tom, 
    assays=assay_tom, 
    survey=survey_tom,
    method=geo.DesurveyingMethod.MINIMUM_CURVATURE,
)

Like Pandas, we can use describe on a GeoLime GeoRefObject.

In [ ]:
dh_tom.describe()

The following methods give us insights on the number of holes ans samples of a Drillholes object.

In [ ]:
len(dh_tom.holeids())

In [ ]:
dh_tom.element_count()

Data can be plotted on a 2D map colored by continuous or categorical properties. Here are displayed the different prospects, which are used to add another subselection of deposits within the entire MacPass project.

In [ ]:
dh_tom.plot_2d(property="Prospect", agg_method="first", interactive_map=True)

Numerical Data can be specified as category using the `categorical` boolean parameter.

In [ ]:
dh_tom.plot_2d(property="Year", agg_method="first", interactive_map=True, categorical=True)

## 3D Visualisation

In [ ]:
dh_tom_pv = dh_tom.to_pyvista('Zn_pct')
tom_topo_pv = tom_topo.to_pyvista()

In [ ]:
pl = pv.Plotter()

pl.add_mesh(dh_tom_pv.tube(radius=10))
pl.add_mesh(tom_topo_pv, opacity=0.7)

pl.show()

### Add Satellite Image

In [ ]:
ds = rioxarray.open_rasterio("../data/TOM.tif")

In [ ]:
ds = ds.rio.reproject("EPSG:26909")

In [ ]:
## Fetch the texture as an image
image = np.moveaxis(ds.values, 0, -1)

## Create the ground control points for texture mapping
o = ds.x.min(), ds.y.min(), 0.0 # Bottom Left
u = ds.x.max(), ds.y.min(), 0.0 # Bottom Right
v = ds.x.min(), ds.y.max(), 0.0 # Lop left
## Note: Z-coordinate doesn't matter

## Use the GCPs to map the tex coords
mapped_surf = tom_topo_pv.texture_map_to_plane(o, u, v)

# Plot using texture 
pl = pv.Plotter()

pl.add_mesh(mapped_surf, texture=pv.numpy_to_texture(image))
pl.add_mesh(dh_tom_pv.tube(radius=10))

pl.show()

## Exploration of different Prospects

`set` transforms any sequence to a set of unique values. We can also the `unique` fonction from numpy in order to have the unique values as a numpy array.

In [ ]:
set(dh_tom['Prospect'])

In [ ]:
prospect_list = np.unique(dh_tom['Prospect'])

In [ ]:
for prospect in prospect_list:
    hid = dh_tom.data("HOLEID", f'Prospect == "{prospect}"')
    print(f"Prospect {prospect} has {len(set(hid))} holes")

Mean values of Zinc in the Tom East prospect can be displayed using the region filter in the plot_2d method

In [ ]:
dh_tom.plot_2d(
    property="Zn_pct", 
    agg_method="mean", 
    region="Prospect == 'Tom East'",
    region_agg='all',
    interactive_map=True
)

## Export GeoLime File

In [ ]:
dh_tom.to_file("../data/dh_tom")